In [1]:
import os
import time

import pandas as pd
import numpy as np
import cv2
import matplotlib.pyplot as plt
import tensorflow as tf
from tensorflow.keras import datasets, layers, models, callbacks, optimizers
from keras.utils.vis_utils import plot_model

from lib.data_normalizer import draw_image_with_boxes

# Make numpy values easier to read.
np.set_printoptions(precision=3, suppress=True)

IMAGE_SHAPE = (227,227)

2022-11-14 05:57:46.882447: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-11-14 05:57:47.843755: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libdirectml.d6f03b303ac3c4f2eeb8ca631688c9757b361310.so
2022-11-14 05:57:47.843817: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libdxcore.so
2022-11-14 05:57:47.845911: I tensorflow/c/logging.cc:34] Successfully opened dynamic library libd3d12.so
2022-11-14 05:57:47.974616: I tensorflow/c/logging.cc:34] DirectML device enumeration: found 1 compatible adapters.


## Modelo de identificación de placas

In [2]:
N_mobile = tf.keras.applications.NASNetMobile( input_tensor = layers.Input(
    shape=(IMAGE_SHAPE[0], IMAGE_SHAPE[1], 3)),
    include_top=False,
    weights='imagenet'
    )

# Let's create a function that will construct our model
def create_model(no_of_classes):

    # Freeze the whole model
    N_mobile.trainable = False

    # Start by taking the output feature maps from NASNETMobile
    base_model_output = N_mobile.output

    # Convert to a single-dimensional vector by Global Average Pooling.

    # We could also use Flatten()(x) but GAP is more effective, it reduces
    # Parameters and controls overfitting.
    flattened_output = layers.GlobalAveragePooling2D()(base_model_output)

    # Create our Classification Head, final layer contains
    # Ouput units = no. classes
    class_prediction = layers.Dense(256, activation="relu")(flattened_output)
    class_prediction = layers.Dense(128, activation="relu")(class_prediction )
    class_prediction = layers.Dropout(0.2)(class_prediction)
    class_prediction = layers.Dense(64, activation="relu")(class_prediction)
    class_prediction = layers.Dropout(0.2)(class_prediction )
    class_prediction = layers.Dense(32, activation="relu")(class_prediction)
    class_prediction = layers.Dense(no_of_classes, activation='softmax',
                                    name="class_output")(class_prediction)

    # Create Our Localization Head, final layer contains 4 nodes for x1,y1,x2,y2
    # Respectively.
    box_output = layers.Dense(256, activation="relu")(flattened_output)
    box_output = layers.Dense(128, activation="relu")(box_output)
    box_output = layers.Dropout(0.2)(box_output )

    box_output = layers.Dense(64, activation="relu")(box_output)
    box_output = layers.Dropout(0.2)(box_output )

    box_output = layers.Dense(32, activation="relu")(box_output)
    box_predictions = layers.Dense(4, activation='sigmoid',
                            name= "box_output")(box_output)

    # Now combine the two heads
    model = models.Model(inputs=N_mobile.input, outputs= [box_predictions,
                                                   class_prediction])

    return model

# Create the model for 1 class
model = create_model(1); print("Model Created")

# plot_model(model, to_file='model_plot.png', show_shapes=True, 
#            show_layer_names=True)

2022-11-14 05:57:50.963490: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-11-14 05:57:50.964288: I tensorflow/c/logging.cc:34] DirectML: creating device on adapter 0 (AMD Radeon R9 200 Series)
2022-11-14 05:57:51.027398: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2022-11-14 05:57:51.027429: W tensorflow/core/common_runtime/pluggable_device/pluggable_device_bfc_allocator.cc:28] Overriding allow_growth setting because force_memory_growth was requested by the device.
2022-11-14 05:57:51.027448: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_

Model Created
